In [78]:
import requests, json, shelve, time
from pathlib import Path

# Documentation :)
https://alternative.me/crypto/api/

# Testing dependency code

In [22]:
# Generate endpoint URLs
listings_endpoint = "https://api.alternative.me/v2/listings"

In [24]:
# GET endpoint
listings_response = requests.get(listsings_endpoint)
all_listings = listings_response.json()

In [25]:
slugs = []
for coin in all_listings['data']:
    slugs.append(coin['website_slug'])
print(slugs)

['bitcoin', 'litecoin', 'namecoin', 'terracoin', 'peercoin', 'novacoin', 'feathercoin', 'mincoin', 'maincoin', 'freicoin', 'ixcoin', 'bitball', 'bitbar', 'wisdom-chain', 'worldcoin', 'digitalcoin', 'goldcoin', 'argentum', 'fastcoin', 'phoenixcoin', 'megacoin', 'infinitecoin', 'primecoin', 'anoncoin', 'casinocoin', 'bullion', 'emerald-crypto', 'ripple', 'quark', 'sexcoin', 'tagcoin', 'i0coin', 'nxt', 'unobtanium', 'joulecoin', 'datacoin', 'dao-casino', 'global-digital-content', 'deutsche-emark', 'dogecoin', 'netcoin', 'diamond', 'hobonickels', 'orbitcoin', 'omni', 'fedoracoin', 'ronpaulcoin', 'racing-pigeon-chain', 'mooncoin', 'dimecoin', '42-coin', 'vertcoin', 'digibyte', 'smartcoin', 'noblecoin', 'reddcoin', 'potcoin', 'maxcoin', 'dash', 'counterparty', 'cachecoin', 'mintcoin', 'dopecoin', 'auroracoin', 'animecoin', 'marscoin', 'pandacoin', 'maza', 'ufocoin', 'blackcoin', 'litbinex-coin', 'litebar', 'photon', 'zeitcoin', 'myriadcoin', 'dnotes', 'einsteinium', 'bitcoin-scrypt', 'ecc', 

In [79]:
slugs[501]

'kyber-network'

In [26]:
len(slugs)

3105

In [29]:
# Generate endpoints from slugs
def _endpoints_from_slugs(slugs: list[str]) -> list[str]:
    """Generates endpoints from a list of website slugs"""
    endpoints = []
    for slug in slugs:
        endpoints.append(f"https://api.alternative.me/v2/ticker/{slug}/")
    return endpoints

In [27]:
# Could be more memory efficient

In [32]:
endpoints = _endpoints_from_slugs(slugs)
print(endpoints[0])

https://api.alternative.me/v2/ticker/bitcoin/


In [36]:
def save_to_txt(txt: str, full_path: Path = Path('./default_name'), flag: str = 'a') -> None:
    """ Saves txt to file at full_path, optionally with flag """
    
    with open(full_path, mode=flag) as file:
        file.write(txt)

In [43]:
# TESTING CODE
for num in range(2):
    response = requests.get(endpoints[num])
    response.raise_for_status()
    j_str = json.dumps(response.json(), indent=True, sort_keys=True)
    
    save_to_txt(j_str, full_path='./all_crypto_saved.txt')

In [52]:
def _get_listings(listings_endpoint: str) -> list:
    listings_response = requests.get(listings_endpoint)
    all_listings = listings_response.json()
    return all_listings

In [50]:
def _get_slugs(all_listings) -> list[str]:
    """
    Get all website slugs from JSON objects.
    Returns: list of slugs
    """
    slugs = []
    for coin in all_listings['data']:
        slugs.append(coin['website_slug'])
    
    return slugs
    

In [57]:
def save_to_shelve(obj, key: str='all_json', file_path: str='./all_json') -> None:
    """ Saves obj to shelve at file_path under key """
    with shelve.open(file_path) as s_file:
            s_file[key] = obj
    

# Get all JSONs here

In [102]:
def get_all_json(listings_endpoint: str="https://api.alternative.me/v2/listings",
                 skip: int=0,
                 is_save: bool=True,
                 shelve_key: str='all_json', 
                 file_path: str='./all_json') -> list[str]:
    """
    Get all available cryto-currency JSON objects from the free crypto API, 
    and optionally, save the JSON objects returned. Handles exceptions gracefully
    by saving progress before exiting.
    
    Return list of JSONs for each coin
    """
    
    if skip: shelve_key += f"_{skip}_onwards"
    
    all_listings = _get_listings(listings_endpoint)
    slugs = _get_slugs(all_listings)
    
    print(f"Skipping the first {skip} endpoints")
    endpoints = _endpoints_from_slugs(slugs)[skip:]
    
    print(f"Total Endpoints: {len(endpoints)}")
    
    # Actually fetches the JSONs
    all_json = []
    
    try:
        print("Requesting data".center(79, '~'))
        for number, endpoint in enumerate(endpoints):
            
            if number % 100 == 0:
                print(f"Request #{number}, estimated time remaining {(len(endpoints) - number) / 60} minutes")
            
            time.sleep(1.5)
                
            response = requests.get(endpoint)
            response.raise_for_status()
            json_response = response.json()
            all_json.append(json.dumps(json_response, sort_keys=True))
    except requests.exceptions.RequestException as e:
        print(f"EXCEPTION!\nRequest to {endpoint} raised exception {e}, preceding to next endpoint.\n")
    except json.JSONDecodeError:
        print(f"JSONDecodeError during json() call of response object {response.text} from "
             f"endpoint {endpoint}")
    finally:
        print("DONE".center(79, '~'))
        if is_save and all_json:
            print(f"Saving to {file_path}, under key: {shelve_key}")
            save_to_shelve(all_json, shelve_key, file_path)
        else:
            print("Skipping save")
                
    print("DONE MAKING REQUESTS".center(79, '~'))
            
    return all_json

In [110]:
all_json_objs = get_all_json(skip=2775)

Skipping the first 2775 endpoints
Total Endpoints: 330
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~Requesting data~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
Request #0, estimated time remaining 5.5 minutes
Request #100, estimated time remaining 3.8333333333333335 minutes
Request #200, estimated time remaining 2.1666666666666665 minutes
Request #300, estimated time remaining 0.5 minutes
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~DONE~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
Saving to ./all_json, under key: all_json_2775_onwards
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~DONE MAKING REQUESTS~~~~~~~~~~~~~~~~~~~~~~~~~~~~~


## My bad :O
### *No servers were harmed in the making of this notebook*
Ok, don't quote me on that.

In [88]:
"""{
	"name": "Fear and Greed Index",
	"data": [
	],
	"metadata": {
		"error": Quota exceeded. Slow down your requests to 60 req/min.
	}
}
"""

'{\n\t"name": "Fear and Greed Index",\n\t"data": [\n\t],\n\t"metadata": {\n\t\t"error": Quota exceeded. Slow down your requests to 60 req/min.\n\t}\n}\n'

## Parse the JSON objects to get only what we want

In [111]:
len(all_json_objs)

330

In [113]:
all_json_objs[329]

'{"data": {"12248": {"circulating_supply": 11655, "id": 12248, "last_updated": 1626944544, "max_supply": 20000, "name": "zzz.finance", "quotes": {"USD": {"market_cap": 8002, "percent_change_1h": null, "percent_change_24h": null, "percent_change_7d": null, "percentage_change_1h": null, "percentage_change_24h": null, "percentage_change_7d": null, "price": 0.686575, "volume_24h": 0}}, "rank": 2476, "symbol": "ZZZ", "total_supply": 11655, "website_slug": "zzz-finance"}}, "metadata": {"error": null, "num_cryptocurrencies": 3105, "timestamp": 1626944544}}'

In [183]:
with shelve.open('./all_json') as file:
    keys = list(file.keys())
    for key in keys:
        print(file[key])

['{"data": {"1": {"circulating_supply": 18896418, "id": 1, "last_updated": 1639082281, "max_supply": 21000000, "name": "Bitcoin", "quotes": {"USD": {"market_cap": 898444455125, "percent_change_1h": -0.779429988047198, "percent_change_24h": -6.24858514037801, "percent_change_7d": -16.833519327241, "percentage_change_1h": -0.779429988047198, "percentage_change_24h": -6.24858514037801, "percentage_change_7d": -16.833519327241, "price": 47546.0, "volume_24h": 26487903760}}, "rank": 1, "symbol": "BTC", "total_supply": 18896418, "website_slug": "bitcoin"}}, "metadata": {"error": null, "num_cryptocurrencies": 3105, "timestamp": 1639082281}}', '{"data": {"2": {"circulating_supply": 69153171, "id": 2, "last_updated": 1639082363, "max_supply": 84000000, "name": "Litecoin", "quotes": {"USD": {"market_cap": 10593815945, "percent_change_1h": -1.01516932588695, "percent_change_24h": -6.8176393936105, "percent_change_7d": -26.5156320141649, "percentage_change_1h": -1.01516932588695, "percentage_chang

In [209]:
with shelve.open('./all_json', flag='r') as file:
    all_meta_info = []
    all_quotes_usd = []
    
    print(f"All keys: {list(file.keys())}")
    for key in list(file.keys()):
        coins = file[key]
        for coin in coins:
            coin_data_dict = json.loads(coin)['data']
            #print(f"coin_data_dict looks like: {coin_data_dict}")
            for special_key in list(coin_data_dict.keys()):
                meta_info_dict = coin_data_dict[special_key]
                print(f"meta_info_dict: {meta_info_dict}")
                meta_info_dict.pop('website_slug')
                meta_info_dict.pop('rank')
                meta_info_dict.pop('last_updated')
                meta_info_dict.pop('total_supply')
                meta_info_dict.pop('id')
                
                
                quotes_usd = meta_info_dict['quotes']['USD']
                quotes_usd.update({'name': meta_info_dict['name']})
                all_quotes_usd.append(quotes_usd)
                
                meta_info_dict.pop('quotes')
                all_meta_info.append(meta_info_dict)
                
                
'''print(f"All META INFO: {all_meta_info}")
print(f"\n\n\nALL QUOTES: {all_quotes_usd}")
'''
len(all_meta_info) == len(all_quotes_usd)

All keys: ['all_json', 'all_json_1521_onwards', 'all_json_2753_onwards', 'all_json_2775_onwards', 'master_df']
meta_info_dict: {'circulating_supply': 18896418, 'id': 1, 'last_updated': 1639082281, 'max_supply': 21000000, 'name': 'Bitcoin', 'quotes': {'USD': {'market_cap': 898444455125, 'percent_change_1h': -0.779429988047198, 'percent_change_24h': -6.24858514037801, 'percent_change_7d': -16.833519327241, 'percentage_change_1h': -0.779429988047198, 'percentage_change_24h': -6.24858514037801, 'percentage_change_7d': -16.833519327241, 'price': 47546.0, 'volume_24h': 26487903760}}, 'rank': 1, 'symbol': 'BTC', 'total_supply': 18896418, 'website_slug': 'bitcoin'}
meta_info_dict: {'circulating_supply': 69153171, 'id': 2, 'last_updated': 1639082363, 'max_supply': 84000000, 'name': 'Litecoin', 'quotes': {'USD': {'market_cap': 10593815945, 'percent_change_1h': -1.01516932588695, 'percent_change_24h': -6.8176393936105, 'percent_change_7d': -26.5156320141649, 'percentage_change_1h': -1.01516932588

JSONDecodeError: Expecting value: line 1 column 1 (char 0)

In [210]:
all_meta_info

[{'circulating_supply': 18896418,
  'max_supply': 21000000,
  'name': 'Bitcoin',
  'symbol': 'BTC'},
 {'circulating_supply': 69153171,
  'max_supply': 84000000,
  'name': 'Litecoin',
  'symbol': 'LTC'},
 {'circulating_supply': 15828050,
  'max_supply': 21000000,
  'name': 'Namecoin',
  'symbol': 'NMC'},
 {'circulating_supply': 22935396,
  'max_supply': 42000000,
  'name': 'Terracoin',
  'symbol': 'TRC'},
 {'circulating_supply': 27047999,
  'max_supply': 2000000000,
  'name': 'Peercoin',
  'symbol': 'PPC'},
 {'circulating_supply': 0,
  'max_supply': 0,
  'name': 'Novacoin',
  'symbol': 'NVC'},
 {'circulating_supply': 246987318,
  'max_supply': 336000000,
  'name': 'Feathercoin',
  'symbol': 'FTC'},
 {'circulating_supply': 0,
  'max_supply': 10000000,
  'name': 'Mincoin',
  'symbol': 'MNC'},
 {'circulating_supply': 315226594,
  'max_supply': 380020246,
  'name': 'MainCoin',
  'symbol': 'MNC'},
 {'circulating_supply': 114195686,
  'max_supply': 100000000,
  'name': 'Freicoin',
  'symbol':

In [211]:
meta_info_df = pd.DataFrame(all_meta_info)
meta_info_df.set_index('name', inplace=True)
meta_info_df

circulating_supply  max_supply symbol
name                                                
Bitcoin                  18896418    21000000    BTC
Litecoin                 69153171    84000000    LTC
Namecoin                 15828050    21000000    NMC
Terracoin                22935396    42000000    TRC
Peercoin                 27047999  2000000000    PPC
...                           ...         ...    ...
Ztranzit Coin                   0     3000000   ZTNZ
Zuplo                           0    18000000    ZLP
Zyro                            0   300000000   ZYRO
ZYX                             0  9000000000    ZYX
zzz.finance                 11655       20000    ZZZ

[3101 rows x 3 columns]

In [212]:
all_quotes_usd

[{'market_cap': 898444455125,
  'percent_change_1h': -0.779429988047198,
  'percent_change_24h': -6.24858514037801,
  'percent_change_7d': -16.833519327241,
  'percentage_change_1h': -0.779429988047198,
  'percentage_change_24h': -6.24858514037801,
  'percentage_change_7d': -16.833519327241,
  'price': 47546.0,
  'volume_24h': 26487903760,
  'name': 'Bitcoin'},
 {'market_cap': 10593815945,
  'percent_change_1h': -1.01516932588695,
  'percent_change_24h': -6.8176393936105,
  'percent_change_7d': -26.5156320141649,
  'percentage_change_1h': -1.01516932588695,
  'percentage_change_24h': -6.8176393936105,
  'percentage_change_7d': -26.5156320141649,
  'price': 153.19,
  'volume_24h': 1188164711,
  'name': 'Litecoin'},
 {'market_cap': 20191061,
  'percent_change_1h': 3.03822500112877,
  'percent_change_24h': 1.25346517986461,
  'percent_change_7d': 14.3646481720056,
  'percentage_change_1h': 3.03822500112877,
  'percentage_change_24h': 1.25346517986461,
  'percentage_change_7d': 14.36464817

In [215]:
quotes_usd_df = pd.DataFrame(all_quotes_usd)
quotes_usd_df.set_index('name', inplace=True)
quotes_usd_df

market_cap  percent_change_1h  percent_change_24h  \
name                                                                 
Bitcoin        898444455125          -0.779430           -6.248585   
Litecoin        10593815945          -1.015169           -6.817639   
Namecoin           20191061           3.038225            1.253465   
Terracoin            452255           5.944261            5.271751   
Peercoin           24927928          -0.223310            0.143550   
...                     ...                ...                 ...   
Ztranzit Coin             0          -1.339305           10.893162   
Zuplo                     0                NaN           -2.884284   
Zyro                      0           7.361045           -3.170483   
ZYX                       0          -7.935788           -7.935788   
zzz.finance            8002                NaN                 NaN   

               percent_change_7d  percentage_change_1h  percentage_change_24h  \
name                                                                            
Bitcoin               -16.833519             -0.779430              -6.248585   
Litecoin              -26.515632             -1.015169              -6.817639   
Namecoin               14.364648              3.038225               1.253465   
Terracoin             -15.372514              5.944261               5.271751   
Peercoin               21.385488             -0.223310               0.143550   
...                          ...                   ...                    ...   
Ztranzit Coin          15.271993             -1.339305              10.893162   
Zuplo                 -76.539984                   NaN              -2.884284   
Zyro                  -53.121708              7.361045              -3.170483   
ZYX                          NaN             -7.935788              -7.935788   
zzz.finance                  NaN                   NaN                    NaN   

               percentage_change_7d         price   volume_24h  
name                                                            
Bitcoin                  -16.833519  47546.000000  26487903760  
Litecoin                 -26.515632    153.190000   1188164711  
Namecoin                  14.364648      1.300000        12606  
Terracoin                -15.372514      0.019958          199  
Peercoin                  21.385488      0.921618         9697  
...                             ...           ...          ...  
Ztranzit Coin             15.271993      2.300000       145188  
Zuplo                    -76.539984      0.000446            0  
Zyro                     -53.121708      0.010022        56931  
ZYX                             NaN      0.002605          534  
zzz.finance                     NaN      0.686575            0  

[3101 rows x 9 columns]

In [220]:
master_df = pd.concat([meta_info_df, quotes_usd_df], axis=1)
master_df

circulating_supply  max_supply symbol    market_cap  \
name                                                                 
Bitcoin                  18896418    21000000    BTC  898444455125   
Litecoin                 69153171    84000000    LTC   10593815945   
Namecoin                 15828050    21000000    NMC      20191061   
Terracoin                22935396    42000000    TRC        452255   
Peercoin                 27047999  2000000000    PPC      24927928   
...                           ...         ...    ...           ...   
Ztranzit Coin                   0     3000000   ZTNZ             0   
Zuplo                           0    18000000    ZLP             0   
Zyro                            0   300000000   ZYRO             0   
ZYX                             0  9000000000    ZYX             0   
zzz.finance                 11655       20000    ZZZ          8002   

               percent_change_1h  percent_change_24h  percent_change_7d  \
name                                                                      
Bitcoin                -0.779430           -6.248585         -16.833519   
Litecoin               -1.015169           -6.817639         -26.515632   
Namecoin                3.038225            1.253465          14.364648   
Terracoin               5.944261            5.271751         -15.372514   
Peercoin               -0.223310            0.143550          21.385488   
...                          ...                 ...                ...   
Ztranzit Coin          -1.339305           10.893162          15.271993   
Zuplo                        NaN           -2.884284         -76.539984   
Zyro                    7.361045           -3.170483         -53.121708   
ZYX                    -7.935788           -7.935788                NaN   
zzz.finance                  NaN                 NaN                NaN   

               percentage_change_1h  percentage_change_24h  \
name                                                         
Bitcoin                   -0.779430              -6.248585   
Litecoin                  -1.015169              -6.817639   
Namecoin                   3.038225               1.253465   
Terracoin                  5.944261               5.271751   
Peercoin                  -0.223310               0.143550   
...                             ...                    ...   
Ztranzit Coin             -1.339305              10.893162   
Zuplo                           NaN              -2.884284   
Zyro                       7.361045              -3.170483   
ZYX                       -7.935788              -7.935788   
zzz.finance                     NaN                    NaN   

               percentage_change_7d         price   volume_24h  
name                                                            
Bitcoin                  -16.833519  47546.000000  26487903760  
Litecoin                 -26.515632    153.190000   1188164711  
Namecoin                  14.364648      1.300000        12606  
Terracoin                -15.372514      0.019958          199  
Peercoin                  21.385488      0.921618         9697  
...                             ...           ...          ...  
Ztranzit Coin             15.271993      2.300000       145188  
Zuplo                    -76.539984      0.000446            0  
Zyro                     -53.121708      0.010022        56931  
ZYX                             NaN      0.002605          534  
zzz.finance                     NaN      0.686575            0  

[3101 rows x 12 columns]

In [222]:
with shelve.open('./all_json') as file:
    file['cleaned_master_df'] = master_df

In [221]:
master_df = master_df.fillna(0)
master_df

circulating_supply  max_supply symbol    market_cap  \
name                                                                 
Bitcoin                  18896418    21000000    BTC  898444455125   
Litecoin                 69153171    84000000    LTC   10593815945   
Namecoin                 15828050    21000000    NMC      20191061   
Terracoin                22935396    42000000    TRC        452255   
Peercoin                 27047999  2000000000    PPC      24927928   
...                           ...         ...    ...           ...   
Ztranzit Coin                   0     3000000   ZTNZ             0   
Zuplo                           0    18000000    ZLP             0   
Zyro                            0   300000000   ZYRO             0   
ZYX                             0  9000000000    ZYX             0   
zzz.finance                 11655       20000    ZZZ          8002   

               percent_change_1h  percent_change_24h  percent_change_7d  \
name                                                                      
Bitcoin                -0.779430           -6.248585         -16.833519   
Litecoin               -1.015169           -6.817639         -26.515632   
Namecoin                3.038225            1.253465          14.364648   
Terracoin               5.944261            5.271751         -15.372514   
Peercoin               -0.223310            0.143550          21.385488   
...                          ...                 ...                ...   
Ztranzit Coin          -1.339305           10.893162          15.271993   
Zuplo                   0.000000           -2.884284         -76.539984   
Zyro                    7.361045           -3.170483         -53.121708   
ZYX                    -7.935788           -7.935788           0.000000   
zzz.finance             0.000000            0.000000           0.000000   

               percentage_change_1h  percentage_change_24h  \
name                                                         
Bitcoin                   -0.779430              -6.248585   
Litecoin                  -1.015169              -6.817639   
Namecoin                   3.038225               1.253465   
Terracoin                  5.944261               5.271751   
Peercoin                  -0.223310               0.143550   
...                             ...                    ...   
Ztranzit Coin             -1.339305              10.893162   
Zuplo                      0.000000              -2.884284   
Zyro                       7.361045              -3.170483   
ZYX                       -7.935788              -7.935788   
zzz.finance                0.000000               0.000000   

               percentage_change_7d         price   volume_24h  
name                                                            
Bitcoin                  -16.833519  47546.000000  26487903760  
Litecoin                 -26.515632    153.190000   1188164711  
Namecoin                  14.364648      1.300000        12606  
Terracoin                -15.372514      0.019958          199  
Peercoin                  21.385488      0.921618         9697  
...                             ...           ...          ...  
Ztranzit Coin             15.271993      2.300000       145188  
Zuplo                    -76.539984      0.000446            0  
Zyro                     -53.121708      0.010022        56931  
ZYX                        0.000000      0.002605          534  
zzz.finance                0.000000      0.686575            0  

[3101 rows x 12 columns]

In [223]:
master_df.describe()

circulating_supply    max_supply    market_cap  percent_change_1h  \
count        3.101000e+03  3.101000e+03  3.101000e+03        3101.000000   
mean         3.790133e+11  1.308680e+14  6.788204e+08           0.522803   
std          1.481749e+13  7.183140e+15  1.856638e+10           7.798672   
min          0.000000e+00  0.000000e+00  0.000000e+00         -83.807801   
25%          0.000000e+00  9.087860e+05  0.000000e+00           0.000000   
50%          5.861000e+03  8.305975e+07  1.087200e+04           0.000000   
75%          6.485397e+07  1.000000e+09  2.376107e+06           0.802929   
max          6.160373e+14  3.999999e+17  8.984445e+11         282.973519   

       percent_change_24h  percent_change_7d  percentage_change_1h  \
count         3101.000000        3101.000000           3101.000000   
mean             4.719684          17.330326              0.522803   
std            149.605322         106.453279              7.798672   
min            -99.999923        -100.000000            -83.807801   
25%             -4.068950          -0.511665              0.000000   
50%              0.000000           1.375882              0.000000   
75%              0.426777          20.832819              0.802929   
max           6999.388880        3372.440426            282.973519   

       percentage_change_24h  percentage_change_7d          price  \
count            3101.000000           3101.000000    3101.000000   
mean                4.719684             17.330326     497.863757   
std               149.605322            106.453279    4759.179227   
min               -99.999923           -100.000000       0.000000   
25%                -4.068950             -0.511665       0.002264   
50%                 0.000000              1.375882       0.040764   
75%                 0.426777             20.832819       0.998500   
max              6999.388880           3372.440426  136508.000000   

         volume_24h  
count  3.101000e+03  
mean   5.172566e+07  
std    1.225699e+09  
min    0.000000e+00  
25%    2.400000e+01  
50%    2.545000e+03  
75%    1.246130e+05  
max    5.869656e+10

# Final testing code

In [224]:
with shelve.open('./all_json') as file:
    new_obj_df = file['cleaned_master_df']
new_obj_df

circulating_supply  max_supply symbol    market_cap  \
name                                                                 
Bitcoin                  18896418    21000000    BTC  898444455125   
Litecoin                 69153171    84000000    LTC   10593815945   
Namecoin                 15828050    21000000    NMC      20191061   
Terracoin                22935396    42000000    TRC        452255   
Peercoin                 27047999  2000000000    PPC      24927928   
...                           ...         ...    ...           ...   
Ztranzit Coin                   0     3000000   ZTNZ             0   
Zuplo                           0    18000000    ZLP             0   
Zyro                            0   300000000   ZYRO             0   
ZYX                             0  9000000000    ZYX             0   
zzz.finance                 11655       20000    ZZZ          8002   

               percent_change_1h  percent_change_24h  percent_change_7d  \
name                                                                      
Bitcoin                -0.779430           -6.248585         -16.833519   
Litecoin               -1.015169           -6.817639         -26.515632   
Namecoin                3.038225            1.253465          14.364648   
Terracoin               5.944261            5.271751         -15.372514   
Peercoin               -0.223310            0.143550          21.385488   
...                          ...                 ...                ...   
Ztranzit Coin          -1.339305           10.893162          15.271993   
Zuplo                   0.000000           -2.884284         -76.539984   
Zyro                    7.361045           -3.170483         -53.121708   
ZYX                    -7.935788           -7.935788           0.000000   
zzz.finance             0.000000            0.000000           0.000000   

               percentage_change_1h  percentage_change_24h  \
name                                                         
Bitcoin                   -0.779430              -6.248585   
Litecoin                  -1.015169              -6.817639   
Namecoin                   3.038225               1.253465   
Terracoin                  5.944261               5.271751   
Peercoin                  -0.223310               0.143550   
...                             ...                    ...   
Ztranzit Coin             -1.339305              10.893162   
Zuplo                      0.000000              -2.884284   
Zyro                       7.361045              -3.170483   
ZYX                       -7.935788              -7.935788   
zzz.finance                0.000000               0.000000   

               percentage_change_7d         price   volume_24h  
name                                                            
Bitcoin                  -16.833519  47546.000000  26487903760  
Litecoin                 -26.515632    153.190000   1188164711  
Namecoin                  14.364648      1.300000        12606  
Terracoin                -15.372514      0.019958          199  
Peercoin                  21.385488      0.921618         9697  
...                             ...           ...          ...  
Ztranzit Coin             15.271993      2.300000       145188  
Zuplo                    -76.539984      0.000446            0  
Zyro                     -53.121708      0.010022        56931  
ZYX                        0.000000      0.002605          534  
zzz.finance                0.000000      0.686575            0  

[3101 rows x 12 columns]

In [ ]:
# Have fun :)